<a href="https://colab.research.google.com/github/BrianKEverett/County-Line/blob/main/Dissertation2_Everett.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [168]:
!pip install ydata-profiling
from ydata_profiling import ProfileReport
import time, os, sys, re
import zipfile, json, datetime, string
import numpy as np
from statistics import *

import matplotlib.pyplot as plt

import pandas as pd
import pandas_datareader as pdr
from pandas_datareader import wb
from pandas.io.formats.style import Styler
import plotly.express as px

import missingno as msno

from google.colab import files

import seaborn as sns

from google.colab import data_table
data_table.enable_dataframe_formatter()
data_table.max_columns = 50

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

%matplotlib inline

plt.style.use('classic')

In [169]:
permits=pd.read_csv("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/Permits.csv")
# dataset can be found here: https://njdca.maps.arcgis.com/home/item.html?id=c754e8f800424bcbb6ad4e6e85b9f736 from NJ Dept of Community Affairs Website.
#this dataset was chosen mostly to assist with my dissertation proposal - I am seeking to explore the behaviors of planning boards in New Jersey, and one hypothesis I have is that planning board decisions are influenced by the effects of the County Line Balloting system, which is unique to 19 out of 21 counties in New Jersey. No other state in the US runs primary elections in this way.
#More on the County Line can be found here by Julia Sass Rubin: https://www.njpp.org/wp-content/uploads/2021/01/NJPP-Report-Does-the-County-Line-Matter-Update-wiht-Final-Vote-Counts.pdf

taxes=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/mediantax.csv")
# dataset can be retireved via: https://njdca.maps.arcgis.com/apps/webappviewer/index.html?id=96ec274c50a34890b23263f101e4ad9b from NJ Department of Community Affairs
# Another hypothesis I have is that the public narrative put forth by planning board members when approving controversial permits, "this will increase rateables for the township, lowering your taxes", does not actually come to fruition
#This data set is helpful for exploring that narrative, and seeing if the opposite is occurring, i.e. more development actually yields higher property taxes

#health=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/countyhealth.csv")
#dataset can be found here: https://www.countyhealthrankings.org/explore-health-rankings/rankings-data-documentation from County Health Rankings and Roadmaps, for 2022 to match same year of data for permits dataset
#With County Health Data, we can infer hypotheses about rates of development and the effect on well-being, liveability.

#Problem with health data set == only 22 observations for New Jersey, not a good sample.

municodes=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/Municodes.csv")
#Data file of all NJ municiaplities, and counties, with the corresponding municipalitiy DCA code. This data file will be most helpful for matching and merging.

#crime=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/CamdenCrime.csv") #not a good format for reading data!
#Dataset can be retireved here: https://www.nj.gov/njsp/ucr/uniform-crime-reports.shtml on the NJ Office of the Attorney General's website
#This crime data is important to consider when analyzing planning and zoning. Does any specific type of development correlate with increased crime? Can liveability theory be worked in here for whether or not communities have what they need to prevent crime?

jobs=pd.read_csv('https://raw.githubusercontent.com/BrianKEverett/County-Line/main/jobsdensity.csv')
#dataset can be built via the table selections on the NJ Community Affairs website - https://njdca.maps.arcgis.com/apps/webappviewer/index.html?id=96ec274c50a34890b23263f101e4ad9b
#Job density is a good variable to consider regarding new large dollar permits. Are some places growing more than others? Can this be attribute to the phenomenon of the County Line?

countysize=pd.read_csv('https://raw.githubusercontent.com/BrianKEverett/County-Line/main/NJCountySize.csv')
#dataset can be found via Wikipedia via 2020 census data - https://en.wikipedia.org/wiki/List_of_counties_in_New_Jersey

njtowns=pd.read_csv('https://raw.githubusercontent.com/BrianKEverett/County-Line/main/NJMunicipalities.csv')
#Dataset can be found at: https://en.wikipedia.org/wiki/List_of_municipalities_in_New_Jersey#:~:text=The%20largest%20municipality%20by%20population,most%20populous%20being%20South%20Carolina.

In [170]:
permits = permits.rename(columns={'DCA MUNI CODE': 'DCA'})
permits = permits.rename(columns={'MUNICIPALITY': 'Municipality'})
permits["Municipality"]= permits["Municipality"].str.title()
permits['Municipality'] = permits['Municipality'].str.replace(' Boro', '')
permits['Municipality'] = permits['Municipality'].str.replace(' Twp', '')
permits['Municipality'] = permits['Municipality'].str.replace(' City', '')
del permits['ID']
del permits['BLOCK NUMBER']
del permits['PAMS PIN']
del permits['USE GROUP']
del permits['YCOORD']
del permits['XCOORD']
del permits['MATCH TYPE']
del permits['LOT NUMBER']
del permits['DATE ISSUED']
del permits['TAX CODE']


del municodes['MUNICIPALITY_NAME_NJ-1040']
del municodes['MUNICIPALITY_CODE_DCA']
del municodes['MUNICIPALITY_NAME_DCA']
del municodes['MUNICIPALITY_CODE_GNIS']
del municodes['MUNICIPALITY_NAME_GNIS']
del municodes['MUNICIPALITY_CODE_FIPS']
municodes = municodes.rename(columns={'MUNICIPALITY_NAME_COMMON': 'Municipality'})
municodes = municodes.rename(columns={'MUNICIPALITY_CODE_NJ-1040': 'DCA'})
municodes = municodes.rename(columns={'COUNTY_NAME_COMMON': 'County'})
municodes['County'] = municodes['County'].str.replace(' County', '')
municodes = municodes.set_index('Municipality')

countysize['Largest City Population']=countysize['Largest City Population'].str.replace(',','')

njtowns['Municipality'] = njtowns['Municipality'].str.replace(' Borough', '')
njtowns['Municipality'] = njtowns['Municipality'].str.replace(' Township', '')
njtowns['Municipality'] = njtowns['Municipality'].str.replace(' City', '')
del njtowns['Municipality Type']
del njtowns['Incorporated[5]']
del njtowns['Form of government']
njtowns = njtowns.set_index('Municipality')
permits = permits.rename(columns={'TYPE': 'Permits'})

del njtowns['Population density']
del njtowns['Land Area (km^2)']
del njtowns['Pop. Change']


#jobs = jobs.set_index('Municipality')
del jobs['JobsVintage']
del jobs['Blk_Grp_Name']
del jobs['JobsDensity']

#taxes = taxes.set_index('Municipality')
del taxes['Tract_Name']
del taxes['Data_Vintage']
del taxes[' ']


njtowns
permits
jobs
taxes
municodes

County  Population (2020)  Population (2010)  \
Municipality                                                     
Aberdeen        Monmouth              19329              18157   
Absecon         Atlantic               9137               8411   
Alexandria     Hunterdon               4809               4938   
Allamuchy         Warren               5335               4323   
Allendale         Bergen               6848               6505   
...                  ...                ...                ...   
Woodlynne         Camden               2902               2978   
Woodstown          Salem               3678               3505   
Woolwich      Gloucester              12577              10200   
Wrightstown   Burlington                720                802   
Wyckoff           Bergen              16585              16635   

              Land area (mi^2)  
Municipality                    
Aberdeen                 5.444  
Absecon                  5.468  
Alexandria              27.534  
Allamuchy               19.992  
Allendale                3.097  
...                        ...  
Woodlynne                0.218  
Woodstown                1.575  
Woolwich                21.072  
Wrightstown              1.850  
Wyckoff                  6.591  

[564 rows x 4 columns]

DCA Municipality                                    Use Group Label  \
0      101      Absecon                                         Mercantile   
1      101      Absecon                                        Educational   
2      102     Atlantic  Clubs, Dance Halls, Casinos, Restaurants, Tave...   
3      102     Atlantic                   Residential (1 & 2 Family Homes)   
4      102     Atlantic    Churches, Libraries, Arcades, Comm. Halls, Gyms   
...    ...          ...                                                ...   
9778  2121   Washington                   Residential (1 & 2 Family Homes)   
9779  2122   Washington                   Residential (1 & 2 Family Homes)   
9780  2122   Washington                                        Educational   
9781  2122   Washington                                           Business   
9782  2122   Washington                                           Business   

     Permits WORK VALUE  
0        NEW    695,000  
1        ALT  4,000,000  
2        ALT  2,100,000  
3        ALT  2,100,000  
4        ALT    337,400  
...      ...        ...  
9778     ALT  1,000,000  
9779     ALT    426,124  
9780     ALT    742,000  
9781     ALT    276,000  
9782     ALT    515,000  

[9783 rows x 5 columns]

Municipality      County  Jobs
0     West Caldwell Township       Essex  4376
1     West Caldwell Township       Essex    28
2     West Caldwell Township       Essex  1939
3            Monroe Township  Gloucester   226
4     West Deptford Township  Gloucester   156
...                      ...         ...   ...
1995       Marlboro Township    Monmouth    90
1996       Marlboro Township    Monmouth   243
1997       Marlboro Township    Monmouth  2738
1998          Dumont Borough      Bergen    10
1999          Dumont Borough      Bergen   592

[2000 rows x 3 columns]

County          Municipality  Median_RE_Taxes
0      Somerset  Bridgewater Township          10000.0
1      Somerset     Bernards Township          10000.0
2      Somerset     Franklin Township           9604.0
3     Middlesex   Woodbridge Township           9041.0
4     Middlesex   Woodbridge Township           7496.0
...         ...                   ...              ...
1641   Somerset     Franklin Township          10000.0
1642   Somerset     Franklin Township           6600.0
1643   Somerset     Franklin Township          10000.0
1644   Somerset     Bernards Township          10000.0
1645   Somerset     Bernards Township          10000.0

[1646 rows x 3 columns]

County   DCA
Municipality                        
Absecon               Atlantic   101
Atlantic City         Atlantic   102
Brigantine            Atlantic   103
Buena Borough         Atlantic   104
Buena Vista Township  Atlantic   105
...                        ...   ...
Phillipsburg            Warren  2119
Pohatcong Township      Warren  2120
Washington Borough      Warren  2121
Washington Township     Warren  2122
White Township          Warren  2123

[564 rows x 2 columns]

In [171]:
permits2 = municodes.merge(permits, how='inner', on=['DCA'])
permits2
permits3 = permits2.groupby('Municipality').agg({'Permits': 'count'})
permits3
print (permits3)

County   DCA Municipality  \
0     Atlantic   101      Absecon   
1     Atlantic   101      Absecon   
2     Atlantic   102     Atlantic   
3     Atlantic   102     Atlantic   
4     Atlantic   102     Atlantic   
...        ...   ...          ...   
9778    Warren  2121   Washington   
9779    Warren  2122   Washington   
9780    Warren  2122   Washington   
9781    Warren  2122   Washington   
9782    Warren  2122   Washington   

                                        Use Group Label Permits WORK VALUE  
0                                            Mercantile     NEW    695,000  
1                                           Educational     ALT  4,000,000  
2     Clubs, Dance Halls, Casinos, Restaurants, Tave...     ALT  2,100,000  
3                      Residential (1 & 2 Family Homes)     ALT  2,100,000  
4       Churches, Libraries, Arcades, Comm. Halls, Gyms     ALT    337,400  
...                                                 ...     ...        ...  
9778                   Residential (1 & 2 Family Homes)     ALT  1,000,000  
9779                   Residential (1 & 2 Family Homes)     ALT    426,124  
9780                                        Educational     ALT    742,000  
9781                                           Business     ALT    276,000  
9782                                           Business     ALT    515,000  

[9783 rows x 6 columns]

Permits
Municipality             
Aberdeen                5
Absecon                 2
Alexandria             11
Allamuchy               4
Allendale              10
...                   ...
Woodbury Heights        1
Woodcliff Lake         19
Woodland Park           8
Woolwich               25
Wyckoff                30

[462 rows x 1 columns]

                  Permits
Municipality             
Aberdeen                5
Absecon                 2
Alexandria             11
Allamuchy               4
Allendale              10
...                   ...
Woodbury Heights        1
Woodcliff Lake         19
Woodland Park           8
Woolwich               25
Wyckoff                30

[462 rows x 1 columns]


In [172]:
permits4 = permits3.merge(njtowns, how='inner', on=['Municipality'])
permits4

Permits      County  Population (2020)  Population (2010)  \
Municipality                                                                  
Aberdeen                5    Monmouth              19329              18157   
Absecon                 2    Atlantic               9137               8411   
Alexandria             11   Hunterdon               4809               4938   
Allamuchy               4      Warren               5335               4323   
Allendale              10      Bergen               6848               6505   
...                   ...         ...                ...                ...   
Woodbury Heights        1  Gloucester               3098               3055   
Woodcliff Lake         19      Bergen               6128               5730   
Woodland Park           8     Passaic              13484              11819   
Woolwich               25  Gloucester              12577              10200   
Wyckoff                30      Bergen              16585              16635   

                  Land area (mi^2)  
Municipality                        
Aberdeen                     5.444  
Absecon                      5.468  
Alexandria                  27.534  
Allamuchy                   19.992  
Allendale                    3.097  
...                            ...  
Woodbury Heights             1.246  
Woodcliff Lake               3.376  
Woodland Park                2.939  
Woolwich                    21.072  
Wyckoff                      6.591  

[476 rows x 5 columns]

In [173]:
jobs['id'] = jobs.groupby(['Municipality','County']).ngroup()
jobs

Municipality      County  Jobs   id
0     West Caldwell Township       Essex  4376  289
1     West Caldwell Township       Essex    28  289
2     West Caldwell Township       Essex  1939  289
3            Monroe Township  Gloucester   226  169
4     West Deptford Township  Gloucester   156  290
...                      ...         ...   ...  ...
1995       Marlboro Township    Monmouth    90  159
1996       Marlboro Township    Monmouth   243  159
1997       Marlboro Township    Monmouth  2738  159
1998          Dumont Borough      Bergen    10   63
1999          Dumont Borough      Bergen   592   63

[2000 rows x 4 columns]

In [174]:
agg_functions = {'Jobs': 'sum', 'Municipality': 'first', 'County': 'first'}
jobs2 = jobs.groupby(jobs['id']).aggregate(agg_functions)
jobs2

Jobs            Municipality      County
id                                            
0        0                      --       Ocean
1     1394       Aberdeen Township    Monmouth
2      755     Alexandria Township   Hunterdon
3     4243       Allendale Borough      Bergen
4     1072        Andover Township      Sussex
..     ...                     ...         ...
302  48129     Woodbridge Township   Middlesex
303    137           Woodbury City  Gloucester
304   5390  Woodcliff Lake Borough      Bergen
305   3786       Woolwich Township  Gloucester
306    126     Wrightstown Borough  Burlington

[307 rows x 3 columns]

In [175]:
jobs2 = jobs2.drop(labels=0, axis=0)
jobs2

Jobs            Municipality      County
id                                            
1     1394       Aberdeen Township    Monmouth
2      755     Alexandria Township   Hunterdon
3     4243       Allendale Borough      Bergen
4     1072        Andover Township      Sussex
5     4993        Asbury Park City    Monmouth
..     ...                     ...         ...
302  48129     Woodbridge Township   Middlesex
303    137           Woodbury City  Gloucester
304   5390  Woodcliff Lake Borough      Bergen
305   3786       Woolwich Township  Gloucester
306    126     Wrightstown Borough  Burlington

[306 rows x 3 columns]

In [176]:
jobs2['Municipality'] = jobs2['Municipality'].str.replace(' Borough', '')
jobs2['Municipality'] = jobs2['Municipality'].str.replace(' Township', '')
jobs2['Municipality'] = jobs2['Municipality'].str.replace(' City', '')
jobs2

Jobs    Municipality      County
id                                    
1     1394        Aberdeen    Monmouth
2      755      Alexandria   Hunterdon
3     4243       Allendale      Bergen
4     1072         Andover      Sussex
5     4993     Asbury Park    Monmouth
..     ...             ...         ...
302  48129      Woodbridge   Middlesex
303    137        Woodbury  Gloucester
304   5390  Woodcliff Lake      Bergen
305   3786        Woolwich  Gloucester
306    126     Wrightstown  Burlington

[306 rows x 3 columns]

In [177]:
permits5 = permits4.merge(jobs2, how='inner', on=['Municipality'])
permits5

Municipality  Permits    County_x  Population (2020)  \
0          Aberdeen        5    Monmouth              19329   
1        Alexandria       11   Hunterdon               4809   
2         Allendale       10      Bergen               6848   
3           Andover        4      Sussex                595   
4           Andover        4      Sussex               5996   
..              ...      ...         ...                ...   
318      Wood-Ridge        7      Bergen              10137   
319      Woodbridge       70   Middlesex             103639   
320        Woodbury        9  Gloucester               9963   
321  Woodcliff Lake       19      Bergen               6128   
322        Woolwich       25  Gloucester              12577   

     Population (2010)  Land area (mi^2)   Jobs    County_y  
0                18157             5.444   1394    Monmouth  
1                 4938            27.534    755   Hunterdon  
2                 6505             3.097   4243      Bergen  
3                  606             1.348   1072      Sussex  
4                 6319            20.044   1072      Sussex  
..                 ...               ...    ...         ...  
318               7626             1.114   2452      Bergen  
319              99585            23.258  48129   Middlesex  
320              10174             2.020    137  Gloucester  
321               5730             3.376   5390      Bergen  
322              10200            21.072   3786  Gloucester  

[323 rows x 8 columns]

In [178]:
del permits5['County_y']
permits5 = permits5.rename(columns={'County_x': 'County'})
permits5

Municipality  Permits      County  Population (2020)  \
0          Aberdeen        5    Monmouth              19329   
1        Alexandria       11   Hunterdon               4809   
2         Allendale       10      Bergen               6848   
3           Andover        4      Sussex                595   
4           Andover        4      Sussex               5996   
..              ...      ...         ...                ...   
318      Wood-Ridge        7      Bergen              10137   
319      Woodbridge       70   Middlesex             103639   
320        Woodbury        9  Gloucester               9963   
321  Woodcliff Lake       19      Bergen               6128   
322        Woolwich       25  Gloucester              12577   

     Population (2010)  Land area (mi^2)   Jobs  
0                18157             5.444   1394  
1                 4938            27.534    755  
2                 6505             3.097   4243  
3                  606             1.348   1072  
4                 6319            20.044   1072  
..                 ...               ...    ...  
318               7626             1.114   2452  
319              99585            23.258  48129  
320              10174             2.020    137  
321               5730             3.376   5390  
322              10200            21.072   3786  

[323 rows x 7 columns]

In [179]:
permits5['id'] = permits5.groupby(['Municipality','County']).ngroup()
permits5

Municipality  Permits      County  Population (2020)  \
0          Aberdeen        5    Monmouth              19329   
1        Alexandria       11   Hunterdon               4809   
2         Allendale       10      Bergen               6848   
3           Andover        4      Sussex                595   
4           Andover        4      Sussex               5996   
..              ...      ...         ...                ...   
318      Wood-Ridge        7      Bergen              10137   
319      Woodbridge       70   Middlesex             103639   
320        Woodbury        9  Gloucester               9963   
321  Woodcliff Lake       19      Bergen               6128   
322        Woolwich       25  Gloucester              12577   

     Population (2010)  Land area (mi^2)   Jobs   id  
0                18157             5.444   1394    0  
1                 4938            27.534    755    1  
2                 6505             3.097   4243    2  
3                  606             1.348   1072    3  
4                 6319            20.044   1072    3  
..                 ...               ...    ...  ...  
318               7626             1.114   2452  269  
319              99585            23.258  48129  270  
320              10174             2.020    137  271  
321               5730             3.376   5390  272  
322              10200            21.072   3786  273  

[323 rows x 8 columns]

In [180]:
agg_functions = {'Municipality': 'first', 'County': 'first', 'Permits': 'first', 'Jobs': 'sum', 'Population (2020)': 'first', 'Population (2010)': 'first', 'Land area (mi^2)': 'first'}
permits6 = permits5.groupby(permits5['id']).aggregate(agg_functions)
permits6

Municipality      County  Permits   Jobs  Population (2020)  \
id                                                                   
0          Aberdeen    Monmouth        5   1394              19329   
1        Alexandria   Hunterdon       11    755               4809   
2         Allendale      Bergen       10   4243               6848   
3           Andover      Sussex        4   2144                595   
4       Asbury Park    Monmouth       21   4993              15188   
..              ...         ...      ...    ...                ...   
269      Wood-Ridge      Bergen        7   2452              10137   
270      Woodbridge   Middlesex       70  48129             103639   
271        Woodbury  Gloucester        9    137               9963   
272  Woodcliff Lake      Bergen       19   5390               6128   
273        Woolwich  Gloucester       25   3786              12577   

     Population (2010)  Land area (mi^2)  
id                                        
0                18157             5.444  
1                 4938            27.534  
2                 6505             3.097  
3                  606             1.348  
4                16008             1.429  
..                 ...               ...  
269               7626             1.114  
270              99585            23.258  
271              10174             2.020  
272               5730             3.376  
273              10200            21.072  

[274 rows x 7 columns]

In [181]:
taxes['Municipality'] = taxes['Municipality'].str.replace(' Borough', '')
taxes['Municipality'] = taxes['Municipality'].str.replace(' Township', '')
taxes['Municipality'] = taxes['Municipality'].str.replace(' City', '')

taxes['id'] = taxes.groupby(['County','Municipality']).ngroup()
taxes

County Municipality  Median_RE_Taxes   id
0      Somerset  Bridgewater          10000.0  293
1      Somerset     Bernards          10000.0  289
2      Somerset     Franklin           9604.0  295
3     Middlesex   Woodbridge           9041.0  176
4     Middlesex   Woodbridge           7496.0  176
...         ...          ...              ...  ...
1641   Somerset     Franklin          10000.0  295
1642   Somerset     Franklin           6600.0  295
1643   Somerset     Franklin          10000.0  295
1644   Somerset     Bernards          10000.0  289
1645   Somerset     Bernards          10000.0  289

[1646 rows x 4 columns]

In [182]:
agg_functions = {'Median_RE_Taxes': 'median', 'Municipality': 'first', 'County': 'first'}
taxes = taxes.groupby(taxes['id']).aggregate(agg_functions)
taxes

Median_RE_Taxes       Municipality  County
id                                             
0            10000.0          Allendale  Bergen
1            10000.0             Alpine  Bergen
2            10000.0        Bergenfield  Bergen
3            10000.0             Bogota  Bergen
4             8347.0          Carlstadt  Bergen
..               ...                ...     ...
366           7622.0             Oxford  Warren
367           4731.0  Phillipsburg Town  Warren
368           7670.0          Pohatcong  Warren
369           8351.5         Washington  Warren
370           5715.0              White  Warren

[371 rows x 3 columns]

In [183]:
permits7 = permits6.merge(taxes, how='inner', on=['Municipality'])
permits7

Municipality    County_x  Permits   Jobs  Population (2020)  \
0              Aberdeen    Monmouth        5   1394              19329   
1             Allendale      Bergen       10   4243               6848   
2               Andover      Sussex        4   2144                595   
3           Asbury Park    Monmouth       21   4993              15188   
4    Atlantic Highlands    Monmouth        2   1404               4414   
..                  ...         ...      ...    ...                ...   
254             Wharton      Morris        3   1392               7241   
255         Willingboro  Burlington        6   1207              31889   
256          Wood-Ridge      Bergen        7   2452              10137   
257          Woodbridge   Middlesex       70  48129             103639   
258      Woodcliff Lake      Bergen       19   5390               6128   

     Population (2010)  Land area (mi^2)  Median_RE_Taxes    County_y  
0                18157             5.444           9866.0    Monmouth  
1                 6505             3.097          10000.0      Bergen  
2                  606             1.348           9274.0      Sussex  
3                16008             1.429           7315.0    Monmouth  
4                 4385             1.264           9308.0    Monmouth  
..                 ...               ...              ...         ...  
254               6522             2.072           8079.0      Morris  
255              31629             7.725           5857.0  Burlington  
256               7626             1.114           9413.0      Bergen  
257              99585            23.258           8759.0   Middlesex  
258               5730             3.376          10000.0      Bergen  

[259 rows x 9 columns]

In [184]:
del permits7 ['County_y']
permits7 = permits7.rename(columns={'County_x': 'County'})
permits7 = permits7.rename(columns={'Median_RE_Taxes': 'Median Property Taxes'})
permits7

Municipality      County  Permits   Jobs  Population (2020)  \
0              Aberdeen    Monmouth        5   1394              19329   
1             Allendale      Bergen       10   4243               6848   
2               Andover      Sussex        4   2144                595   
3           Asbury Park    Monmouth       21   4993              15188   
4    Atlantic Highlands    Monmouth        2   1404               4414   
..                  ...         ...      ...    ...                ...   
254             Wharton      Morris        3   1392               7241   
255         Willingboro  Burlington        6   1207              31889   
256          Wood-Ridge      Bergen        7   2452              10137   
257          Woodbridge   Middlesex       70  48129             103639   
258      Woodcliff Lake      Bergen       19   5390               6128   

     Population (2010)  Land area (mi^2)  Median Property Taxes  
0                18157             5.444                 9866.0  
1                 6505             3.097                10000.0  
2                  606             1.348                 9274.0  
3                16008             1.429                 7315.0  
4                 4385             1.264                 9308.0  
..                 ...               ...                    ...  
254               6522             2.072                 8079.0  
255              31629             7.725                 5857.0  
256               7626             1.114                 9413.0  
257              99585            23.258                 8759.0  
258               5730             3.376                10000.0  

[259 rows x 8 columns]

#Final Dataset based on Municipalities is almost finished.

##Need to go back and edit the way I changed Boro vs Borough etc. I fear I've lost data along the way given things like "Franklin Boro" and "Franklin Township" being different municipalities within the same county.

##Also need to add a code or column indicating County Line or not.